# Hand Landmarks Dection with MediaPipe Tasks Python API

## 1. Install Dependencies

In [1]:
!pip install -q mediapipe==0.10.0 opencv-python

## 2. Download model
Then download an off-the-shelf model bundle. Check out the [MediaPipe documentation](https://developers.google.com/mediapipe/solutions/vision/hand_landmarker#models) for more information about this model bundle.

In [2]:
!wget -q https://storage.googleapis.com/mediapipe-models/hand_landmarker/hand_landmarker/float16/1/hand_landmarker.task

wget: /Users/gmx/.netrc:1: unknown token "-e"


## 3. Import the necessary modules

In [1]:
# Import the necessary modules
import cv2
import mediapipe as mp
from mediapipe import solutions
from mediapipe.framework.formats import landmark_pb2
import numpy as np

In [4]:

BaseOptions = mp.tasks.BaseOptions
HandLandmarker = mp.tasks.vision.HandLandmarker
HandLandmarkerOptions = mp.tasks.vision.HandLandmarkerOptions
HandLandmarkerResult = mp.tasks.vision.HandLandmarkerResult
VisionRunningMode = mp.tasks.vision.RunningMode

# options = HandLandmarkerOptions(
#     base_options=BaseOptions(model_asset_path='hand_landmarker.task'),
#     num_hands=2)


cap = cv2.VideoCapture(0)
RESULT = None
timestamp = 0

MARGIN = 10  # pixels
FONT_SIZE = 1
FONT_THICKNESS = 1
HANDEDNESS_TEXT_COLOR = (88, 205, 54) # vibrant green

def draw_landmarks_on_image(rgb_image, detection_result):
    hand_landmarks_list = detection_result.hand_landmarks
    
    handedness_list = detection_result.handedness
    annotated_image = np.copy(rgb_image)

    # Loop through the detected hands to visualize.
    for idx in range(len(hand_landmarks_list)):
        hand_landmarks = hand_landmarks_list[idx]
        handedness = handedness_list[idx]

        # Draw the hand landmarks.
        hand_landmarks_proto = landmark_pb2.NormalizedLandmarkList()
        hand_landmarks_proto.landmark.extend([
          landmark_pb2.NormalizedLandmark(x=landmark.x, y=landmark.y, z=landmark.z) for landmark in hand_landmarks
        ])
        solutions.drawing_utils.draw_landmarks(
            annotated_image,
            hand_landmarks_proto,
            solutions.hands.HAND_CONNECTIONS,
            solutions.drawing_styles.get_default_hand_landmarks_style(),
            solutions.drawing_styles.get_default_hand_connections_style())
        # Get the top left corner of the detected hand's bounding box.
        height, width, _ = annotated_image.shape
        x_coordinates = [landmark.x for landmark in hand_landmarks]
        y_coordinates = [landmark.y for landmark in hand_landmarks]
        text_x = int(min(x_coordinates) * width)
        text_y = int(min(y_coordinates) * height) - MARGIN

        # Draw handedness (left or right hand) on the image.
        cv2.putText(annotated_image, f"{handedness[0].category_name}",
            (text_x, text_y), cv2.FONT_HERSHEY_DUPLEX,
            FONT_SIZE, HANDEDNESS_TEXT_COLOR, FONT_THICKNESS, cv2.LINE_AA)
    
    return annotated_image


# Create a hand landmarker instance with the live stream mode:
def print_result(result: HandLandmarkerResult, output_image: mp.Image, timestamp_ms: int):
    global RESULT
    RESULT = result
    print('hand landmarker result: {}'.format(RESULT))

options = HandLandmarkerOptions(
    base_options=BaseOptions(model_asset_path='hand_landmarker.task'),
    running_mode=VisionRunningMode.LIVE_STREAM,
    result_callback=print_result,
    num_hands=2)

In [5]:
with HandLandmarker.create_from_options(options) as landmarker:
    # The landmarker is initialized. Use it here.
    while cap.isOpened(): # Capture frame-by-frame
        ret, frame = cap.read()
        if not ret:
            print("Ignoring empty frmae")
            break
        timestamp += 1
        
        # Flip on horizontal 图像水平翻转，镜像
        frame = cv2.flip(frame, 1)
        
        # frame_timestamp_ms = int(cap.get(cv2.CAP_PROP_POS_MSEC))  
        mp_image = mp.Image(image_format=mp.ImageFormat.SRGB, data=frame)

        # Detections
        landmarker.detect_async(mp_image,timestamp)
        
        # Rendering results
        if(not (RESULT is None)):
            annotated_image = draw_landmarks_on_image(mp_image.numpy_view(), RESULT)
            cv2.imshow('Hand Tracking', annotated_image)
            print("showing detected image")
            
            # Save our image    
#             cv2.imwrite(os.path.join('Output Images', '{}.jpg'.format(uuid.uuid1())), annotated_image)
          
        else:
            cv2.imshow('Hand Tracking', frame)

        if cv2.waitKey(5) & 0xFF == ord('q'):
            print("Closing Camera Stream")
            break
            
cap.release()
cv2.destroyAllWindows()  

hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing

hand landmarker result: HandLandmarkerResult(handedness=[[Category(index=0, score=0.9755347967147827, display_name='Left', category_name='Left')]], hand_landmarks=[[NormalizedLandmark(x=0.06378071755170822, y=0.8518791198730469, z=3.863206927690044e-07, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.1333998292684555, y=0.7921352386474609, z=-0.016847718507051468, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.1794828325510025, y=0.6915786862373352, z=-0.011213939636945724, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.19071882963180542, y=0.5858885049819946, z=-0.006674517877399921, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.18032941222190857, y=0.505316436290741, z=-0.0013208547607064247, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.17026692628860474, y=0.6260253190994263, z=0.038517020642757416, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.18945574760437012, y=0.535313069820404, z=0.039934512227773666, visibility=0.0, presence=0.0), 

hand landmarker result: HandLandmarkerResult(handedness=[[Category(index=0, score=0.9834897518157959, display_name='Left', category_name='Left')]], hand_landmarks=[[NormalizedLandmark(x=0.08619499206542969, y=0.835841178894043, z=3.4151955219385854e-07, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.16103440523147583, y=0.7895436882972717, z=-0.011489706113934517, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.2125050127506256, y=0.6888111233711243, z=-0.0018983973423019052, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.22696319222450256, y=0.5811010003089905, z=0.00665271608158946, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.22103223204612732, y=0.5122248530387878, z=0.015896189957857132, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.19670486450195312, y=0.6110683083534241, z=0.0373733825981617, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.21969100832939148, y=0.519788920879364, z=0.04023570194840431, visibility=0.0, presence=0.0), Norm

showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[[Category(index=0, score=0.960065484046936, display_name='Left', category_name='Left')]], hand_landmarks=[[NormalizedLandmark(x=0.12027472257614136, y=0.8172237277030945, z=3.224813553970307e-07, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.19071801006793976, y=0.780833899974823, z=-0.011493813246488571, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.2445916384458542, y=0.6828804016113281, z=-0.003960772883147001, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.26856204867362976, y=0.5839859247207642, z=0.0025680605322122574, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.2652233839035034, y=0.5122482180595398, z=0.009607375599443913, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.23174121975898743, y=0.6036768555641174, z=0.024824045598506927, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.2584879398345947, y=0.5109415650367737, z=0.021603239700198174, visibility=

hand landmarker result: HandLandmarkerResult(handedness=[[Category(index=0, score=0.976019561290741, display_name='Left', category_name='Left')]], hand_landmarks=[[NormalizedLandmark(x=0.13587018847465515, y=0.8127327561378479, z=3.6466076380747836e-07, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.20819811522960663, y=0.7797601222991943, z=-0.01513170637190342, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.2653126120567322, y=0.6796461939811707, z=-0.00832722894847393, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.2922733724117279, y=0.575901985168457, z=-0.0018793395720422268, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.28751397132873535, y=0.5009763836860657, z=0.00528024323284626, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.2496752291917801, y=0.5932173132896423, z=0.025913985446095467, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.27741795778274536, y=0.5011460185050964, z=0.024171141907572746, visibility=0.0, presence=0.0), Norm

...

showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[[Category(index=0, score=0.972234308719635, display_name='Left', category_name='Left')]], hand_landmarks=[[NormalizedLandmark(x=0.2735830545425415, y=0.7601385712623596, z=4.685883538968483e-07, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.33972662687301636, y=0.7564648985862732, z=-0.020483825355768204, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.4033970534801483, y=0.6799255609512329, z=-0.020879855379462242, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.45189377665519714, y=0.6064262390136719, z=-0.021179329603910446, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.4907180666923523, y=0.5566970705986023, z=-0.020490143448114395, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.4029041528701782, y=0.5753300189971924, z=0.011194654740393162, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.45127278566360474, y=0.5131889581680298, z=-0.0035890592262148857, visibili

hand landmarker result: HandLandmarkerResult(handedness=[[Category(index=0, score=0.9717448353767395, display_name='Left', category_name='Left')]], hand_landmarks=[[NormalizedLandmark(x=0.2676388919353485, y=0.7688888311386108, z=4.777081699103292e-07, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.3350145220756531, y=0.7586277723312378, z=-0.019636401906609535, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.39691779017448425, y=0.6811851859092712, z=-0.02076892741024494, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.4446343183517456, y=0.6089601516723633, z=-0.022125117480754852, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.48425623774528503, y=0.5606949925422668, z=-0.02256748452782631, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.39612919092178345, y=0.5773772597312927, z=0.01085595041513443, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.444301038980484, y=0.5143777132034302, z=-0.005078029353171587, visibility=0.0, presence=0.0), Norm

hand landmarker result: HandLandmarkerResult(handedness=[[Category(index=0, score=0.9760757088661194, display_name='Left', category_name='Left')]], hand_landmarks=[[NormalizedLandmark(x=0.16661977767944336, y=0.9255775809288025, z=4.4656027853307023e-07, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.23954090476036072, y=0.9111922979354858, z=-0.019592953845858574, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.30929437279701233, y=0.7930871844291687, z=-0.01658226177096367, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.35205990076065063, y=0.6910279989242554, z=-0.013886211439967155, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.3880831003189087, y=0.623210608959198, z=-0.010872665792703629, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.29731786251068115, y=0.6766692399978638, z=0.012273445725440979, visibility=0.0, presence=0.0), NormalizedLandmark(x=0.3469786047935486, y=0.5901058316230774, z=-0.0019425986101850867, visibility=0.0, presence=0.0)

showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_worl

showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_world_landmarks=[])
showing detected image
hand landmarker result: HandLandmarkerResult(handedness=[], hand_landmarks=[], hand_worl